In [5]:
import keras
import numpy as np
from sklearn.preprocessing import scale
import math

import numpy as np
import scipy as sp
import pandas as pd
import sklearn as sl
from pandas import DataFrame, Series
from scipy import sparse

from sklearn.preprocessing import LabelBinarizer
from sklearn.preprocessing import OneHotEncoder

from sklearn.metrics.pairwise import cosine_similarity

from sklearn.metrics.pairwise import euclidean_distances

from sklearn.metrics.pairwise import rbf_kernel


import scipy.io as sio

Using TensorFlow backend.


In [6]:
################### Sport and Daily Activity dataset ####################
##### dataset path ######
fn = 'data/'

### activity labels
acts = ['a01', 'a02', 'a03', 'a04', 'a05','a06', 'a07','a08','a09','a10', 'a11','a12','a13','a14','a15','a16', 'a17', 'a18', 'a19']

### segment labels
segs = ['s01', 's02', 's03', 's04', 's05','s06', 's07','s08','s09','s10', 's11','s12','s13','s14','s15','s16', 's17', 's18', 's19', 's20',
        's21', 's22', 's23', 's24', 's25','s26', 's27','s28','s29','s30', 's31','s32','s33','s34','s35','s36', 's37', 's38', 's39', 's40',
        's41', 's42', 's43', 's44', 's45','s46', 's47','s48','s49','s50', 's51','s52','s53','s54','s55','s56', 's57', 's58', 's59', 's60',]

### sensor names
sensors = ['acc','gyro', 'magnet']

#### the axis index in each file for different sensor locations
locs = {"T": 0, "RA" : 9, "LA" : 18,"RL" : 27,"LL":36}

### user ids in the dataset format
users = ['p1', 'p2', 'p3', 'p4', 'p5', 'p6', 'p7', 'p8']

###############################################################


def selected_locations(nodes, locs, num_sensors):
    start = 1
    for n in nodes:
        if start == 1:
            start = 0
            idx = np.arange(locs[n], locs[n] + 9)
        else:
            idx = np.concatenate((idx, np.arange(locs[n], locs[n] + 3 * num_sensors)))
    return idx

def extract_features(x):
    numrows = len(x)    # 3 rows in your example
    mean = np.mean(x, axis = 0)
    std = np.std(x, axis = 0)
    var = np.var(x, axis = 0)
    median = np.median(x, axis = 0)
    xmax = np.amax(x, axis = 0)
    xmin =np.amax(x, axis = 0)
    p2p = xmax - xmin
    amp = xmax - mean
    s2e = x[numrows-1,:] - x[0,:]
    features = np.concatenate([mean, std, var, median, xmax, xmin, p2p, amp, s2e])#, morph]);
    return features





def data_generate(users_idx, acts_idx, segs_idx, fn, nodes, num_sensors):
    start = 0
    idx = selected_locations(nodes, locs, num_sensors)

    for u in users_idx:
        for s in segs_idx:
            for a in acts_idx:
                filename = fn + acts[a] + '/' + users[u] + '/' + segs[s] + '.txt'
                raw_data = np.genfromtxt(filename, delimiter=',', skip_header=0)
                raw_data = raw_data[:,idx]
                f = extract_features(raw_data)
                if start == 0:
                    fsp = f
                    label = a + 1
                    start = 1
                else: 
                    fsp = np.vstack((fsp, f))
                    label = np.vstack((label, a+1))
    return scale(fsp, axis = 0), label

In [7]:
acts_idx = range(0,19)
users_t = range(0,8)
segs_idx = range(0,60)
nodes = ["T", "LL", "RL", "LA", "RA"]

count = 1

for user in users_t:
    print("read the data for user %d" %(user+1))
    fspace, labels = data_generate([user], acts_idx, segs_idx, fn, nodes, num_sensors = 3)
    fspace

    cache_data_new = pd.DataFrame(fspace)
    cache_label_new = pd.DataFrame(labels)

    if count == 1:
        data_new = pd.DataFrame(fspace)
        label_new = pd.DataFrame(labels)
        count += 1

       


    else:
        data_new = data_new.append(cache_data_new, ignore_index=True)
        label_new = label_new.append(cache_label_new, ignore_index=True)

read the data for user 1
read the data for user 2
read the data for user 3
read the data for user 4
read the data for user 5
read the data for user 6
read the data for user 7
read the data for user 8


In [8]:
label_new = label_new[0]

In [9]:
result = pd.concat([data_new, label_new], axis=1, join='inner')

In [10]:
import scipy.io as sio
from itertools import cycle
from sklearn.linear_model import Perceptron
from sklearn.model_selection import train_test_split

In [11]:
x_train, x_test, y_train, y_test = train_test_split(data_new, label_new, test_size = 0.9, random_state = 139)

In [35]:
from sklearn.linear_model import Perceptron
import time
import random

def b_sampling_perc(X, Y, x_test, y_test):
    
    #print(X)
    start = time.process_time()
    count = 0
    beta = {0.001 : 0.01, 0.01 : 0.1, 0.1 : 1}
    
    classifier = Perceptron()
    classifier.fit(X, Y)
    print(np.abs(classifier.decision_function(X)).shape)
    #print(np.argmin(np.abs(classifier.decision_function(X))))

    #sample = X[np.argmin(np.abs(classifier.decision_function(X)), axis=0)]
    #print(sample.shape)
    #print(X.shape)
    
   
    arr = classifier.decision_function(x_test)
  #  print(arr)
    score_train = classifier.score(X, Y)
    print(score_train)
    
#     y_train = pd.DataFrame(y_train)
#     y_test = pd.DataFrame(y_test)

    beta_t_array = []
    beta_score_array = []
    
    for key, value in beta.items():
        print(key, value)
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
        
        
        for index, row in x_test.iterrows():

            if (count < 20):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))
            
                z = ((random.random()*value) < (key / (key + abs(y_hat))))

                if (z == 1):
                    count += 1   
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]       
                    x_train = x_train.append(a)
                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
            else:
                classifier.fit(x_train, y_train)
                count = 0

            count_for +=1
    
        score_test = classifier.score(x_test, y_test)
        beta_t_array.append(t)
        beta_score_array.append(score_test)
        

    end = time.process_time()
    print("time takes for Perceptron= {} min".format((end - start) / 60))
    
    return(beta_t_array, beta_score_array)
    

In [36]:
beta_t_array, beta_score_array = b_sampling_perc(x_train, y_train, x_test, y_test)

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)


(912, 19)
0.9089912280701754
0.001 0.01


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

0.01 0.1


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

0.1 1


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

time takes for Perceptron= 0.43645833333333334 min


In [27]:
beta_t_perc = [145, 146, 139]

In [28]:
x_train.shape

(912, 405)

In [28]:
beta_score_perc = [0.9195906432748538, 0.9398148148148148, 0.9507797270955166]

In [46]:
plt.plot([0.001, 0.01, 0.1], beta_t_perc, color = "red", marker="o", label = "Perceptron")
plt.plot([0.001, 0.01, 0.1], beta_t_svm, color = "blue", marker="o", label = "Linear SVM")
plt.title("b-sampling", loc = 'center')
plt.xlabel("b parameters")
plt.ylabel("label requests")
plt.legend(loc='upper left')
plt.savefig("b-sampling.png")
plt.close()

In [13]:
from sklearn.svm import LinearSVC
import time

def sampling_svm(X, Y, x_test, y_test):

    start = time.process_time()
    count = 0
    
    classifier = LinearSVC(C=10**-1, multi_class='crammer_singer')
    classifier.fit(X, Y)
    
    score_train = classifier.score(X, Y)
    print(score_train)
    
    beta = {0.001 : 0.01, 0.01 : 0.1, 0.1 : 1}
    beta_t_array = []
    beta_score_array = []
    
    for key, value in beta.items():
        print(key, value)
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
    
        for index, row in x_test.iterrows():
            if (count < 10):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))

                z = ((random.random() * value) < (key / (key + abs(y_hat))))

                if (z == True):
                    count += 1
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]
                    x_train = x_train.append(a)

                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
            else:
                classifier.fit(x_train, y_train)
                count = 0

            count_for +=1
    
        score_test = classifier.score(x_test, y_test)
        beta_t_array.append(t)
        beta_score_array.append(score_test)

    end = time.process_time()
    print("time takes = {} min".format((end - start) / 60))

    return(beta_t_array, beta_score_array)

In [14]:
beta_t_array, beta_score_array = sampling_svm(x_train, y_train, x_test, y_test)

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


1.0
0.001 0.01


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblin

0.01 0.1


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblin

0.1 1


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblin

time takes = 6.041145833333333 min


In [29]:
beta_t_svm = [144, 160, 142]

In [30]:
beta_score_svm = [0.9790448343079922, 0.9780701754385965, 0.9785575048732943]

In [15]:
from sklearn.linear_model import Perceptron
import time
import random
import math

def logistic_sampling_perc(X, Y, x_test, y_test):
    start = time.process_time()
    
    count = 0
    gamma = [1, 2, 4, 8]
    classifier = Perceptron()
    classifier.fit(X, Y)

    score_train = classifier.score(X, Y)
    print(score_train)

    gamma_t_array = []
    gamma_score_array = []
    
    for key, value in enumerate(gamma):
        print(key, value)
        
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
        
        for index, row in x_test.iterrows():
            if (count < 10):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))
                z = ((random.random()) < math.exp(-value*abs(y_hat)))

                if (z == 1):
                    count += 1   
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]       
                    x_train = x_train.append(a)
                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
                    
                else:
                    classifier.fit(x_train, y_train)
                    count = 0

            count_for +=1

        score_test = classifier.score(x_test, y_test)
        gamma_t_array.append(t)
        gamma_score_array.append(score_test)

    end = time.process_time()
    print("time takes = {} min".format((end - start) / 60))

    return(gamma_t_array, gamma_score_array)

In [ ]:
gamma_t_array, gamma_score_array = logistic_sampling_perc(x_train, y_train, x_test, y_test)

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

0.9089912280701754
0 1


C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

...

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)
C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\linear_model\stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in Perceptron in 0.19. If b

In [31]:
gamma_t_perc = [251, 69, 13, 0]

In [32]:
gamma_score_perc = [0.9416423001949318, 0.94432261208577, 0.9328703703703703, 0.8942495126705653]

In [20]:
from sklearn.svm import LinearSVC
import time

def logistic_sampling_svm(X, Y, x_test, y_test):

    start = time.process_time()
    count = 0
    
    classifier = LinearSVC(C=10**-1, multi_class='crammer_singer')
    classifier.fit(X, Y)
    
    score_train = classifier.score(X, Y)
    print(score_train)
    
    gamma = [1, 2, 4, 8]
    gamma_t_array = []
    gamma_score_array = []
    
    for key, value in enumerate(gamma):
        print(key, value)
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
    
        for index, row in x_test.iterrows():
            if (count < 10):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))

                z = ((random.random()) < math.exp(-value*abs(y_hat)))

                if (z == True):
                    count += 1
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]
                    x_train = x_train.append(a)

                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
            else:
                classifier.fit(x_train, y_train)
                count = 0

            count_for +=1
    
        score_test = classifier.score(x_test, y_test)
        gamma_t_array.append(t)
        gamma_score_array.append(score_test)

    end = time.process_time()
    print("time takes = {} min".format((end - start) / 60))

    return(gamma_t_array, gamma_score_array)

In [21]:
gamma_t_array_svm, gamma_score_array_svm = logistic_sampling_svm(x_train, y_train, x_test, y_test)

1.0
0 1
1 2
2 4
3 8
time takes = 5.3375 min


In [33]:
gamma_t_array_svm = [265, 87, 5, 1]

In [35]:
gamma_score_array_svm = [0.9777046783625731,
 0.9774610136452242,
 0.9774610136452242,
 0.9774610136452242]

In [47]:
plt.plot([1, 2, 4, 8], gamma_t_perc, color = "red", marker="o", label = "Perceptron")
plt.plot([1, 2, 4, 8], gamma_t_array_svm, color = "blue", marker="o", label = "Linear SVM")
plt.title("logistic-sampling", loc = 'center')
plt.xlabel("gamma parameters")
plt.ylabel("label requests")
plt.legend(loc='upper left')
plt.savefig("logistic-sampling.png")
plt.close()

In [60]:
from sklearn.svm import LinearSVC
import time
import random
import math

def fixed_sampling_perc(X, Y, x_test, y_test):
    start = time.process_time()
    count = 0

    classifier = Perceptron()
    classifier.fit(X, Y)
    score_train = classifier.score(X, Y)
    print(score_train)

    thresholds = [0.04, 0.05, 0.06]
    threshold_t = []
    threshold_t_score = []
    
    for thold in thresholds:
        print(thold)
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
        
        for index, row in x_test.iterrows():
            if (count < 10):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))
                z = (math.exp(-1*abs(y_hat)) < thold)

                if (z == 1):
                    count += 1   
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]       
                    x_train = x_train.append(a)
                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
            else:
                classifier.fit(x_train, y_train)
                count = 0

            count_for +=1
    
        score_test = classifier.score(x_test, y_test)
        threshold_t.append(t)
        threshold_t_score.append(score_test)

    end = time.process_time()
    print("time takes for Perceptron= {} min".format((end - start) / 60))
    return(threshold_t, threshold_t_score)

In [63]:
import warnings

warnings.filterwarnings("ignore")

threshold_t, threshold_t_score = fixed_sampling_perc(x_train, y_train, x_test, y_test)

0.9089912280701754
0.04
0.05
0.06
time takes for Perceptron= 18.5125 min


In [ ]:
threshold_t_score_perc

In [50]:
threshold_t_perc = [6405, 6767, 6770]

In [37]:
threshold_t_score_perc = [0.9896442495126706, 0.991349902534113, 0.9820906432748538]

In [66]:
from sklearn.svm import LinearSVC
from sklearn.linear_model import Perceptron
import time
import random
import math
def fixed_sampling_svm(X, Y, x_test, y_test):
    start = time.process_time()
    count = 0

    classifier = LinearSVC(C=10**-1, multi_class='crammer_singer')
    classifier.fit(X, Y)
    score_train = classifier.score(X, Y)
    print(score_train)

    thresholds = [0.04, 0.05, 0.06]
    threshold_t = []
    threshold_t_score = []
    
    for thold in thresholds:
        print(thold)
        t = 0
        count_for = 0
        x_train = X.copy()
        y_train = Y.copy()
        
        for index, row in x_test.iterrows():
            if (count < 10):
                y_hat = (classifier.predict(x_test.iloc[count_for:(count_for+1),:]))
                z = (math.exp(-1*abs(y_hat)) < thold)
                
                if (z == 1):
                    print("value of z", math.exp(-1*abs(y_hat)))
                    count += 1   
                    t += 1
                    a = x_test.iloc[count_for:count_for+1,:]       
                    x_train = x_train.append(a)
                    lab = y_test[index]
                    lab_series = pd.Series(lab)
                    y_train = y_train.append(lab_series,ignore_index=True)
            else:
                classifier.fit(x_train, y_train)
                count = 0

            count_for +=1
    
        score_test = classifier.score(x_test, y_test)
        threshold_t.append(t)
        threshold_t_score.append(score_test)

    end = time.process_time()
    print("time takes for Perceptron= {} min".format((end - start) / 60))
    return(threshold_t, threshold_t_score)

In [ ]:
import warnings

warnings.filterwarnings("ignore")

threshold_t_svm, threshold_t_score_svm = fixed_sampling_svm(x_train, y_train, x_test, y_test)

1.0
0.04
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 0.00033546262790251185
value of z 2.2603294069810542e-06
value of z 0.01831563888873418
value of z 5.602796437537268e-09
value of z 1.670170079024566e-05
value of z 6.14421235332821e-06
value of z 0.006737946999085467
value of z 1.1253517471925912e-07
value of z 4.139937718785167e-08
value of z 1.522997974471263e-08
value of z 1.1253517471925912e-07
value of z 6.14421235332821e-06
value of z 0.00033546262790251185
value of z 8.315287191035679e-07
value of z 4.139937718785167e-08
value of z 3.059023205018258e-07
value of z 1.1253517471925912e-07
value of z 0.006737946999085467
value of z 1.522997974471263e-08
value of z 0.00033546262790251185
value of z 1.522997974471263e-08
value of z 1.522997974471263e-08
value of z 1.1253517471925912e-07
value of z 3.059023205018258e-07
value of z 1.522997974471263e-08
value of z 0.0009118819655545162
value of z 3.059023205018258e-07
value of z 0.0009118819655545162
v

value of z 0.00012340980408667956
value of z 5.602796437537268e-09
value of z 3.059023205018258e-07
value of z 0.00012340980408667956
value of z 4.139937718785167e-08
value of z 3.059023205018258e-07
value of z 0.00012340980408667956
value of z 3.059023205018258e-07
value of z 0.00033546262790251185
value of z 3.059023205018258e-07
value of z 4.139937718785167e-08
value of z 2.2603294069810542e-06
value of z 6.14421235332821e-06
value of z 5.602796437537268e-09
value of z 1.1253517471925912e-07
value of z 6.14421235332821e-06
value of z 6.14421235332821e-06
value of z 0.0024787521766663585
value of z 0.00033546262790251185
value of z 4.5399929762484854e-05
value of z 4.139937718785167e-08
value of z 0.00033546262790251185
value of z 2.2603294069810542e-06
value of z 6.14421235332821e-06
value of z 3.059023205018258e-07
value of z 0.006737946999085467
value of z 0.0024787521766663585
value of z 5.602796437537268e-09
value of z 0.0024787521766663585
value of z 0.00033546262790251185
valu

value of z 0.00033546262790251185
value of z 3.059023205018258e-07
value of z 1.670170079024566e-05
value of z 4.5399929762484854e-05
value of z 2.2603294069810542e-06
value of z 4.5399929762484854e-05
value of z 1.670170079024566e-05
value of z 1.1253517471925912e-07
value of z 4.5399929762484854e-05
value of z 0.0009118819655545162
value of z 6.14421235332821e-06
value of z 0.00012340980408667956
value of z 0.0024787521766663585
value of z 4.139937718785167e-08
value of z 1.670170079024566e-05
value of z 4.5399929762484854e-05
value of z 1.522997974471263e-08
value of z 0.00012340980408667956
value of z 5.602796437537268e-09
value of z 4.139937718785167e-08
value of z 8.315287191035679e-07
value of z 0.006737946999085467
value of z 4.139937718785167e-08
value of z 1.1253517471925912e-07
value of z 1.670170079024566e-05
value of z 4.139937718785167e-08
value of z 6.14421235332821e-06
value of z 1.1253517471925912e-07
value of z 8.315287191035679e-07
value of z 4.139937718785167e-08
va

value of z 0.006737946999085467
value of z 0.00012340980408667956
value of z 1.670170079024566e-05
value of z 0.0024787521766663585
value of z 1.1253517471925912e-07
value of z 8.315287191035679e-07
value of z 2.2603294069810542e-06
value of z 5.602796437537268e-09
value of z 4.139937718785167e-08
value of z 0.0009118819655545162
value of z 1.670170079024566e-05
value of z 2.2603294069810542e-06
value of z 4.5399929762484854e-05
value of z 5.602796437537268e-09
value of z 0.0009118819655545162
value of z 0.0024787521766663585
value of z 3.059023205018258e-07
value of z 2.2603294069810542e-06
value of z 5.602796437537268e-09
value of z 3.059023205018258e-07
value of z 0.0009118819655545162
value of z 5.602796437537268e-09
value of z 0.0009118819655545162
value of z 0.0024787521766663585
value of z 3.059023205018258e-07
value of z 1.522997974471263e-08
value of z 0.00012340980408667956
value of z 2.2603294069810542e-06
value of z 0.0024787521766663585
value of z 0.0024787521766663585
val

value of z 0.00033546262790251185
value of z 2.2603294069810542e-06
value of z 0.0009118819655545162
value of z 0.00033546262790251185
value of z 0.00033546262790251185
value of z 0.006737946999085467
value of z 1.522997974471263e-08
value of z 1.522997974471263e-08
value of z 4.5399929762484854e-05
value of z 8.315287191035679e-07
value of z 4.139937718785167e-08
value of z 0.0009118819655545162
value of z 1.522997974471263e-08
value of z 1.1253517471925912e-07
value of z 4.139937718785167e-08
value of z 0.006737946999085467
value of z 0.0024787521766663585
value of z 0.0024787521766663585
value of z 0.01831563888873418
value of z 0.006737946999085467
value of z 3.059023205018258e-07
value of z 8.315287191035679e-07
value of z 0.01831563888873418
value of z 0.00012340980408667956
value of z 6.14421235332821e-06
value of z 0.00012340980408667956
value of z 1.670170079024566e-05
value of z 1.670170079024566e-05
value of z 0.00033546262790251185
value of z 8.315287191035679e-07
value of 

...

value of z 6.14421235332821e-06
value of z 2.2603294069810542e-06
value of z 0.00012340980408667956
value of z 0.01831563888873418
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 8.315287191035679e-07
value of z 6.14421235332821e-06
value of z 4.5399929762484854e-05
value of z 0.0009118819655545162
value of z 0.01831563888873418
value of z 0.00033546262790251185
value of z 2.2603294069810542e-06
value of z 0.00012340980408667956
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 0.00012340980408667956
value of z 0.01831563888873418
value of z 0.01831563888873418
value of z 4.139937718785167e-08
value of z 1.522997974471263e-08
value of z 8.315287191035679e-07
value of z 4.5399929762484854e-05
value of z 1.522997974471263e-08
value of z 0.006737946999085467
value of z 5.602796437537268e-09
value of z 1.670170079024566e-05
value of z 1.1253517471925912e-07
value of z 0.00033546262790251185
value of z 6.14421235332821e-06
value of z 0.002

value of z 1.522997974471263e-08
value of z 0.01831563888873418
value of z 1.1253517471925912e-07
value of z 3.059023205018258e-07
value of z 0.00012340980408667956
value of z 4.139937718785167e-08
value of z 0.006737946999085467
value of z 0.006737946999085467
value of z 4.139937718785167e-08
value of z 1.1253517471925912e-07
value of z 0.0024787521766663585
value of z 0.00033546262790251185
value of z 5.602796437537268e-09
value of z 0.00012340980408667956
value of z 1.670170079024566e-05
value of z 1.670170079024566e-05
value of z 0.00033546262790251185
value of z 1.1253517471925912e-07
value of z 3.059023205018258e-07
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 1.522997974471263e-08
value of z 4.5399929762484854e-05
value of z 0.0024787521766663585
value of z 1.522997974471263e-08
value of z 4.139937718785167e-08
value of z 1.670170079024566e-05
value of z 8.315287191035679e-07
value of z 5.602796437537268e-09
value of z 3.059023205018258e-07
value of

value of z 0.0024787521766663585
value of z 8.315287191035679e-07
value of z 4.5399929762484854e-05
value of z 0.006737946999085467
value of z 4.5399929762484854e-05
value of z 0.00033546262790251185
value of z 1.670170079024566e-05
value of z 6.14421235332821e-06
value of z 0.00033546262790251185
value of z 6.14421235332821e-06
value of z 0.00033546262790251185
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 1.1253517471925912e-07
value of z 0.01831563888873418
value of z 3.059023205018258e-07
value of z 8.315287191035679e-07
value of z 8.315287191035679e-07
value of z 1.670170079024566e-05
value of z 5.602796437537268e-09
value of z 5.602796437537268e-09
value of z 0.00012340980408667956
value of z 0.00033546262790251185
value of z 0.01831563888873418
value of z 4.5399929762484854e-05
value of z 4.139937718785167e-08
value of z 0.00033546262790251185
value of z 0.00033546262790251185
value of z 0.006737946999085467
value of z 0.00033546262790251185
value of

value of z 8.315287191035679e-07
value of z 1.522997974471263e-08
value of z 8.315287191035679e-07
value of z 5.602796437537268e-09
value of z 4.5399929762484854e-05
value of z 0.00012340980408667956
value of z 8.315287191035679e-07
value of z 4.139937718785167e-08
value of z 5.602796437537268e-09
value of z 0.01831563888873418
value of z 0.006737946999085467
value of z 4.139937718785167e-08
value of z 0.00012340980408667956
value of z 0.0024787521766663585
value of z 6.14421235332821e-06
value of z 0.0009118819655545162
value of z 0.0009118819655545162
value of z 1.1253517471925912e-07
value of z 0.0009118819655545162
value of z 4.139937718785167e-08
value of z 3.059023205018258e-07
value of z 2.2603294069810542e-06
value of z 0.006737946999085467
value of z 2.2603294069810542e-06
value of z 0.01831563888873418
value of z 0.01831563888873418
value of z 0.0009118819655545162
value of z 1.522997974471263e-08
value of z 3.059023205018258e-07
value of z 0.01831563888873418
value of z 2.26

value of z 5.602796437537268e-09
value of z 0.00033546262790251185
value of z 1.1253517471925912e-07
value of z 4.139937718785167e-08
value of z 0.00033546262790251185
value of z 5.602796437537268e-09
value of z 0.00012340980408667956
value of z 0.0024787521766663585
value of z 0.0009118819655545162
value of z 6.14421235332821e-06
value of z 5.602796437537268e-09
value of z 2.2603294069810542e-06
value of z 0.0024787521766663585
value of z 0.00012340980408667956
value of z 0.00033546262790251185
value of z 0.006737946999085467
value of z 0.00033546262790251185
value of z 4.139937718785167e-08
value of z 4.5399929762484854e-05
value of z 0.006737946999085467
value of z 2.2603294069810542e-06
value of z 3.059023205018258e-07
value of z 6.14421235332821e-06
value of z 5.602796437537268e-09
value of z 5.602796437537268e-09
value of z 0.0024787521766663585
value of z 0.0024787521766663585
value of z 2.2603294069810542e-06
value of z 6.14421235332821e-06
value of z 1.522997974471263e-08
valu

In [52]:
threshold_t_svm = [7462, 7462, 7462]

In [39]:
threshold_t_score_svm = [0.9896442495126706, 0.991349902534113, 0.9820906432748538]

In [ ]:
import matplotlibotlibotlib.pyplot as plt

In [51]:
plt.plot([0.5, 0.7, 0.8], threshold_t_perc, color = "red", marker="o", label = "Perceptron")
plt.title("fixed margin sampling", loc = 'center')
plt.xlabel("thresholds")
plt.ylabel("label requests")
plt.legend(loc='upper left')
plt.savefig("fixed margin sampling perceptron.png")
plt.close()

In [53]:
plt.plot([0.5, 0.7, 0.8], threshold_t_svm, color = "blue", marker="o", label = "Linear SVM")
plt.title("fixed margin sampling", loc = 'center')
plt.xlabel("thresholds")
plt.ylabel("label requests")
plt.legend(loc='upper left')
plt.savefig("fixed margin sampling SVM.png")
plt.close()

In [40]:
from sklearn.linear_model import Perceptron
def train_perc(x_train, y_train, x_test, y_test):
    start = time.process_time()

    classifier = Perceptron()
    classifier.fit(x_train, y_train)
    
    score_train = classifier.score(x_train, y_train)
    print(score_train)
    
    score_test = classifier.score(x_test, y_test)
    print(score_test)

    end = time.process_time()
    print("time takes for Perceptron= {} min".format((end - start) / 60))

In [41]:
train_perc(x_train, y_train, x_test, y_test)

0.9089912280701754
0.8942495126705653
time takes for Perceptron= 0.00234375 min


C:\Users\rocki\Anaconda3\lib\site-packages\sklearn\linear_model\stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.perceptron.Perceptron'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)


In [42]:
from sklearn.svm import LinearSVC
import time

def train_svm(x_train, y_train, x_test, y_test):

    start = time.process_time()

    linear_kernel = LinearSVC(C=10**-1, multi_class='crammer_singer')
    linear_kernel.fit(x_train, y_train)
    
    score_train = linear_kernel.score(x_train, y_train)
    print(score_train)
    
    score_test = linear_kernel.score(x_test, y_test)
    print(score_test)

    end = time.process_time()
    print("time takes = {} min".format((end - start) / 60))


In [43]:
train_svm(x_train, y_train, x_test, y_test)

1.0
0.9778265107212476
time takes = 0.08307291666666666 min


In [50]:
"""Abstract class for sampling methods.
Provides interface to sampling methods that allow same signature
for select_batch.  Each subclass implements select_batch_ with the desired
signature for readability.
"""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import abc
import numpy as np

class SamplingMethod(object):
  __metaclass__ = abc.ABCMeta

  @abc.abstractmethod
  def __init__(self, X, y, seed, **kwargs):
    self.X = X
    self.y = y
    self.seed = seed

  def flatten_X(self):
    shape = self.X.shape
    flat_X = self.X
    if len(shape) > 2:
      flat_X = np.reshape(self.X, (shape[0],np.product(shape[1:])))
    return flat_X


  @abc.abstractmethod
  def select_batch_(self):
    return

  def select_batch(self, **kwargs):
    return self.select_batch_(**kwargs)

  def to_dict(self):
    return None

In [55]:
from sklearn.svm import LinearSVC
def select_batch_(X,Y):
    """Returns batch of datapoints with smallest margin/highest uncertainty.
    For binary classification, can just take the absolute distance to decision
    boundary for each point.
    For multiclass classification, must consider the margin between distance for
    top two most likely classes.
    Args:
      model: scikit learn model with decision_function implemented
      already_selected: index of datapoints already selected
      N: batch size
    Returns:
      indices of points selected to add using margin active learner
    """
    linear_kernel = LinearSVC(C=10**-1, multi_class='crammer_singer')
    linear_kernel.fit(X, Y)
    try:
      distances = linear_kernel.decision_function(X)
    except:
      distances = linear_kernel.predict_proba(X)
    if len(distances.shape) < 2:
      min_margin = abs(distances)
    else:
      sort_distances = np.sort(distances, 1)[:, -2:]
      min_margin = sort_distances[:, 1] - sort_distances[:, 0]
    rank_ind = np.argsort(min_margin)
    #rank_ind = [i for i in rank_ind if i not in already_selected]
    #active_samples = rank_ind[0:N]
    return rank_ind

In [59]:
select_batch_(x_train, y_train)

C:\Users\rocki\AppData\Roaming\Python\Python36\site-packages\sklearn\svm\base.py:922: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


array([341, 526, 591, 477, 707, 283, 508, 450, 793, 455, 692, 723, 690,
       833, 207, 543, 877, 299, 694, 160, 103,  78, 387, 673, 712, 756,
       898, 593, 258, 222, 302, 663, 186, 261, 453, 702, 216, 278, 319,
       606, 849, 240, 819, 431, 323, 668, 346, 671, 777, 401, 215, 866,
       360,  57, 288, 171, 607, 357, 771, 555, 482, 693, 423, 740, 897,
       535,  71, 696,  54,  94, 403, 315, 126,   0, 424, 531, 284, 212,
       150, 751, 483, 385, 624, 911, 427, 675, 730, 452, 585, 812, 744,
       674, 660, 310, 617, 459, 577, 454, 734,  73, 474, 618, 855,  61,
       763, 128, 344, 356, 603,   9, 248, 180, 389, 594, 444, 201, 872,
       746, 505, 687, 567, 676, 809, 721, 102, 253, 590, 529, 175, 563,
       629, 722, 485, 814, 716, 830, 679, 776, 775, 799, 778,  82, 554,
       546, 883, 560,  35, 109,  79, 167, 116, 430, 608, 797, 584,  24,
        30,  22, 200, 647, 857, 458, 726,  74, 328, 395,   1, 750,  99,
       747, 388, 678, 698, 655, 845, 891,  50, 520, 123, 610, 62